postgresql에서 label_math_ele뽑아옴

In [1]:
import pandas as pd
from pymongo import MongoClient
from sqlalchemy import create_engine

db_config = {
        'host': "10.41.2.78",
        'port': "5432",
        'user': "postgres",
        'pw': "qwe123",
        'db': "project",
        'table_name': "label_math_ele"
    }
    
db_url = f"postgresql://{db_config['user']}:{db_config['pw']}@{db_config['host']}:{db_config['port']}/{db_config['db']}"
engine = create_engine(db_url)

query = f"SELECT * FROM {db_config['table_name']}"
label_math_ele = pd.read_sql(query, engine)

In [8]:
label_math_ele

from_id from_semester                          from_chapter_name  to_id  \
0         116     중등-중7-1학기                       수와연산 > 소인수분해 > 소인수분해   7944   
1        2615     초등-초5-1학기      자연수의 혼합 계산 > 덧셈과 뺄셈이 섞여 있는 식을 계산해 볼까요   7933   
2        2616     초등-초5-1학기     자연수의 혼합 계산 > 곱셈과 나눗셈이 섞여 있는 식을 계산해 볼까요   2068   
3        2616     초등-초5-1학기     자연수의 혼합 계산 > 곱셈과 나눗셈이 섞여 있는 식을 계산해 볼까요   2073   
4        2617     초등-초5-1학기  자연수의 혼합 계산 > 덧셈, 뺄셈, 곱셈이 섞여 있는 식을 계산해 볼까요   2615   
...       ...           ...                                        ...    ...   
1605    11269     초등-초4-1학기                    큰 수 > 십만, 백만, 천만을 알아볼까요   7268   
1606    11270     초등-초4-1학기                          큰 수 > 억과 조를 알아볼까요  11269   
1607    11271     초등-초4-1학기                          큰 수 > 억과 조를 알아볼까요  11270   
1608     8481     초등-초4-1학기                       각도 > 각도의 합과 차는 얼마일까요   7310   
1609     8247     초등-초4-2학기               삼각형 > 삼각형을 두 가지 기준으로 분류해 볼까요   8832   

                            to_chapter_name to_semester from_g to_g  
0                           곱셈 > 곱셈식을 알아볼까요   초등-초2-1학기     중등   초등  
1                   덧셈과 뺄셈 > 세 수의 계산을 해 볼까요   초등-초2-1학기     초등   초등  
2            곱셈과 나눗셈 > 세 자릿수에 두 자릿수를 곱해 볼까요   초등-초4-1학기     초등   초등  
3       곱셈과 나눗셈 > 세 자릿수를 두 자릿수로 나누어 볼까요 (1)   초등-초4-1학기     초등   초등  
4     자연수의 혼합 계산 > 덧셈과 뺄셈이 섞여 있는 식을 계산해 볼까요   초등-초5-1학기     초등   초등  
...                                     ...         ...    ...  ...  
1605                    큰 수 > 다섯 자릿수를 알아볼까요   초등-초4-1학기     초등   초등  
1606                큰 수 > 십만, 백만, 천만을 알아볼까요   초등-초4-1학기     초등   초등  
1607                      큰 수 > 억과 조를 알아볼까요   초등-초4-1학기     초등   초등  
1608                 덧셈과 뺄셈 > 덧셈을 해 볼까요 (3)   초등-초3-1학기     초등   초등  
1609           삼각형 > 삼각형을 두 가지 기준으로 분류해 볼까요   초등-초4-2학기     초등   초등  

[1610 rows x 8 columns]

mongoDB로 부터 JSON파일을 DataFrame으로 변환

In [2]:
import pandas as pd
from pymongo import MongoClient

# MongoDB 연결 설정
username = 'root'
password = 'qwe123'
host = '10.41.2.78'
port = 27017
client = MongoClient(f'mongodb://{username}:{password}@{host}:{port}/')
db = client['project']

# 컬렉션 선택
qa_collection = db['1_correct_answer']
irt_collection = db['2_questionIRT']
# taker_irt_collection = db['3_candidateIRT']

In [3]:
import pandas as pd
from pymongo import MongoClient
# MongoDB 연결 설정
username = 'root'
password = 'qwe123'
host = '10.41.2.78'
port = 27017
client = MongoClient(f'mongodb://{username}:{password}@{host}:{port}/')
db = client['project']
# 컬렉션 선택
qa_collection = db['1_correct_answer']
irt_collection = db['2_questionIRT']
theta_collection = db['3_candidateIRT']
# taker_irt_collection = db['3_candidateIRT']
# 필요한 필드만 선택하여 데이터를 가져오는 함수
def fetch_collection_as_dataframe(collection, fields):
    data = list(collection.find({}, fields))
    return pd.DataFrame(data)
# 필요한 필드만 선택
qa_fields = {'testID': 1, 'assessmentItemID': 1, 'learnerID': 1, 'answerCode': 1, '_id': 0}
irt_fields = {
    'testID': 1,
    'assessmentItemID': 1,
    'knowledgeTag': 1,
    'difficultyLevel': 1,         # 추가된 필드
    'discriminationLevel': 1,     # 추가된 필드
    'guessLevel': 1,              # 추가된 필드
    '_id': 0
}
theta_fields = {
    'testID': 1,
    'learnerID': 1,
    'theta': 1,                   # 추가된 필드
    '_id': 0
}
# 데이터프레임으로 변환
qa_df = fetch_collection_as_dataframe(qa_collection, qa_fields)
irt_df = fetch_collection_as_dataframe(irt_collection, irt_fields)
theta_df = fetch_collection_as_dataframe(theta_collection, theta_fields)
# 병합 전 필요한 컬럼만 유지 및 인덱스 설정
qa_df = qa_df.set_index(['testID', 'assessmentItemID'])
irt_df = irt_df.set_index(['testID', 'assessmentItemID'])
theta_df = theta_df.set_index(['testID', 'learnerID'])
# 최적화된 병합
merged_df = pd.merge(qa_df, irt_df, left_index=True, right_index=True, how='left')
merged_df = pd.merge(merged_df, theta_df, left_on=['testID', 'learnerID'], right_on=['testID', 'learnerID'], how='left').reset_index()
# 추가된 필드를 포함하여 데이터프레임을 구성
merged_df = merged_df[['learnerID', 'answerCode', 'knowledgeTag', 'difficultyLevel', 'discriminationLevel', 'guessLevel', 'theta']]
merged_df['knowledgeTag'] = pd.to_numeric(merged_df['knowledgeTag'], errors='coerce', downcast='integer')
print(merged_df.head())

    learnerID answerCode  knowledgeTag  difficultyLevel  discriminationLevel  \
0  A010000003          1          5844        -3.719715             0.721179   
1  A010000003          1          5844        -2.917577             1.349719   
2  A010000003          1          5844        -2.273138             1.192981   
3  A010000003          1          5844        -2.302867             1.732754   
4  A010000003          1          5844        -1.611647             1.911265   

   guessLevel     theta  
0    0.010089  0.196765  
1    0.012780  0.196765  
2    0.050128  0.196765  
3    0.006224  0.196765  
4    0.000235  0.196765  


In [9]:
merged_df

learnerID answerCode  knowledgeTag  difficultyLevel  \
0        A010000003          1          5844        -3.719715   
1        A010000003          1          5844        -2.917577   
2        A010000003          1          5844        -2.273138   
3        A010000003          1          5844        -2.302867   
4        A010000003          1          5844        -1.611647   
...             ...        ...           ...              ...   
1677353  A090000552          1          4243         0.012002   
1677354  A090000552          1          4243        -0.725795   
1677355  A090000552          1         10196         0.450923   
1677356  A090000552          1          2648         2.126145   
1677357  A090000552          0          2648         0.038831   

         discriminationLevel    guessLevel     theta  
0                   0.721179  1.008904e-02  0.196765  
1                   1.349719  1.278008e-02  0.196765  
2                   1.192981  5.012783e-02  0.196765  
3                   1.732754  6.223898e-03  0.196765  
4                   1.911265  2.348796e-04  0.196765  
...                      ...           ...       ...  
1677353            54.381941  2.930000e-08  0.785694  
1677354             0.416779  1.159106e-02  0.785694  
1677355             4.251689  0.000000e+00  0.785694  
1677356             0.240034  3.483607e-02  0.785694  
1677357             1.585952  3.879670e-05  0.785694  

[1677358 rows x 7 columns]

postgresql에서 education_2022 dataframe으로 변환 + 전처리

In [4]:
import pandas as pd
from sqlalchemy import create_engine

# 연결 정보 설정
db_config = {
    'host': "10.41.2.78",
    'port': "5432",
    'user': "postgres",
    'pw': "qwe123",
    'db': "project",
    'location': "localhost_target",
    'engine': "postgre",
    'table_name': "education_2022"
}

# 데이터베이스 URL 구성
db_url = f"postgresql://{db_config['user']}:{db_config['pw']}@{db_config['host']}:{db_config['port']}/{db_config['db']}"

# SQLAlchemy를 사용하여 PostgreSQL에 연결하는 엔진 생성
engine = create_engine(db_url)

# SQL 쿼리 정의 (테이블의 모든 데이터를 선택)
query = f"SELECT * FROM {db_config['table_name']}"

# 쿼리 실행 및 결과를 DataFrame으로 변환
education_2022 = pd.read_sql(query, engine)

# 'Unnamed: 6' 컬럼을 제거
education_2022 = education_2022.drop(columns=['Unnamed: 6'], errors='ignore')

# '계열화' 컬럼의 NaN 값을 '정보 없음'으로 대체
education_2022['계열화'] = education_2022['계열화'].fillna('정보 없음')


In [11]:
education_2022

ID                                         Name         영역명  \
0     2048        큰 수 > 억과 조를 알아볼까요 / 큰 수 > 억과 조를 알아볼까요       수와 연산   
1     2049                           큰 수 > 뛰어 세기를 해 볼까요       수와 연산   
2     2050  큰 수 > 수의 크기를 비교해 볼까요 / 큰 수 > 수의 크기를 비교해 볼까요       수와 연산   
3     2052                             각도 > 어느 각이 더 클까요  도형과 측정(도형)   
4     2053                            각도 > 각의 크기는 얼마일까요  도형과 측정(측정)   
..     ...                                          ...         ...   
637  10741                  제곱근과 실수 > 제곱근과 실수 > 무리수와 실수       수와 연산   
638   5141                  제곱근과 실수 > 제곱근과 실수 > 무리수와 실수       수와 연산   
639   5142                제곱근과 실수 > 제곱근과 실수 > 실수의 대소 관계       수와 연산   
640   5921                  제곱근과 실수 > 제곱근과 실수 > 무리수와 실수       수와 연산   
641   4241                           삼각비 > 삼각비 > 삼각비의 값  도형과 측정(측정)   

            내용요소     계열화 grade  
0    다섯 자리 이상의 수   A-4-7   4-1  
1    다섯 자리 이상의 수   A-4-9   4-1  
2    다섯 자리 이상의 수  A-4-10   4-1  
3         도형의 기초   C-3-3   4-1  
4        각도( ° )   D-8-1   4-1  
..           ...     ...   ...  
637      제곱근과 실수   정보 없음   9-1  
638      제곱근과 실수   정보 없음   9-1  
639      제곱근과 실수   정보 없음   9-1  
640      제곱근과 실수   정보 없음   9-1  
641          삼각비   정보 없음   9-2  

[642 rows x 6 columns]

#### merged_df 가중치 계산

In [5]:
import pandas as pd
import torch
import torch.nn as nn
import torch.optim as optim

# Ensure ID column in education_2022 is numeric to match with merged_df's knowledgeTag
education_2022['ID'] = pd.to_numeric(education_2022['ID'], errors='coerce', downcast='integer')

# Merge education_2022 with merged_df on knowledgeTag and ID
merged_df = pd.merge(merged_df, education_2022[['ID', '계열화']], left_on='knowledgeTag', right_on='ID', how='left')

# Drop the redundant 'ID' column after the merge
merged_df = merged_df.drop(columns=['ID'], errors='ignore')

# Ensure columns are numeric (especially answerCode)
merged_df['answerCode'] = pd.to_numeric(merged_df['answerCode'], errors='coerce')  # Converts non-numeric values to NaN
merged_df['difficultyLevel'] = pd.to_numeric(merged_df['difficultyLevel'], errors='coerce')
merged_df['discriminationLevel'] = pd.to_numeric(merged_df['discriminationLevel'], errors='coerce')
merged_df['theta'] = pd.to_numeric(merged_df['theta'], errors='coerce')
merged_df['knowledgeTag'] = pd.to_numeric(merged_df['knowledgeTag'], errors='coerce', downcast='integer')

print(merged_df)


          learnerID  answerCode  knowledgeTag  difficultyLevel  \
0        A010000003           1          5844        -3.719715   
1        A010000003           1          5844        -2.917577   
2        A010000003           1          5844        -2.273138   
3        A010000003           1          5844        -2.302867   
4        A010000003           1          5844        -1.611647   
...             ...         ...           ...              ...   
1677353  A090000552           1          4243         0.012002   
1677354  A090000552           1          4243        -0.725795   
1677355  A090000552           1         10196         0.450923   
1677356  A090000552           1          2648         2.126145   
1677357  A090000552           0          2648         0.038831   

         discriminationLevel    guessLevel     theta    계열화  
0                   0.721179  1.008904e-02  0.196765  C-1-5  
1                   1.349719  1.278008e-02  0.196765  C-1-5  
2                   1

In [13]:
merged_df

learnerID  answerCode  knowledgeTag  difficultyLevel  \
0        A010000003           1          5844        -3.719715   
1        A010000003           1          5844        -2.917577   
2        A010000003           1          5844        -2.273138   
3        A010000003           1          5844        -2.302867   
4        A010000003           1          5844        -1.611647   
...             ...         ...           ...              ...   
1677353  A090000552           1          4243         0.012002   
1677354  A090000552           1          4243        -0.725795   
1677355  A090000552           1         10196         0.450923   
1677356  A090000552           1          2648         2.126145   
1677357  A090000552           0          2648         0.038831   

         discriminationLevel    guessLevel     theta    계열화  
0                   0.721179  1.008904e-02  0.196765  C-1-5  
1                   1.349719  1.278008e-02  0.196765  C-1-5  
2                   1.192981  5.012783e-02  0.196765  C-1-5  
3                   1.732754  6.223898e-03  0.196765  C-1-5  
4                   1.911265  2.348796e-04  0.196765  C-1-5  
...                      ...           ...       ...    ...  
1677353            54.381941  2.930000e-08  0.785694    NaN  
1677354             0.416779  1.159106e-02  0.785694    NaN  
1677355             4.251689  0.000000e+00  0.785694    NaN  
1677356             0.240034  3.483607e-02  0.785694    NaN  
1677357             1.585952  3.879670e-05  0.785694    NaN  

[1677358 rows x 8 columns]

In [50]:
import pandas as pd
import torch
import torch.nn as nn
import torch.optim as optim
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score

# Mapping from letter to numeric area
area_mapping = {'A': 1, 'B': 2, 'C': 3, 'D': 4, 'E': 5}

def convert_to_numeric_area(x):
    if pd.isna(x) or not isinstance(x, str):
        return 'Unknown'  # Handle NaN or invalid data
    parts = x.split('-')
    if len(parts) >= 2:
        area = parts[0]
        number = parts[1]
        numeric_area = area_mapping.get(area, -1)
        if numeric_area != -1:
            return f"{numeric_area}-{number}"  # Convert to numeric area format
    return 'Unknown'

merged_df['trimmed_serialization'] = merged_df['계열화'].apply(convert_to_numeric_area)

# Create a mapping from numeric serialization strings to unique integers
unique_serializations = merged_df['trimmed_serialization'].dropna().unique()
serialization_labels = {label: i for i, label in enumerate(unique_serializations)}

# Update the mapping function to use the numeric labels
def map_serialization(x):
    if pd.isna(x) or not isinstance(x, str):
        return serialization_labels.get('Unknown', -1)  # Handle NaN or invalid data
    return serialization_labels.get(x, -1)  # Map to unique integer or -1 if unknown

# Apply the mapping
merged_df['serialized_area'] = merged_df['trimmed_serialization'].apply(map_serialization)

# Display the DataFrame to check results
print(merged_df)


# Prepare data
features = ['difficultyLevel', 'discriminationLevel', 'theta', 'guessLevel']
X = merged_df[features].values
y = merged_df['answerCode'].values

# Split data
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

# Standardize features
scaler = StandardScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Convert to PyTorch tensors
X_train = torch.tensor(X_train, dtype=torch.float32)
y_train = torch.tensor(y_train, dtype=torch.float32)
X_test = torch.tensor(X_test, dtype=torch.float32)
y_test = torch.tensor(y_test, dtype=torch.float32)

# Define the model
class EnhancedBinaryNN(nn.Module):
    def __init__(self):
        super(EnhancedBinaryNN, self).__init__()
        # 더 깊고 복잡한 네트워크
        self.fc1 = nn.Linear(4, 256)  # 첫 번째 은닉층의 유닛 수를 256으로 증가
        self.fc2 = nn.Linear(256, 128)  # 두 번째 은닉층의 유닛 수를 128로 설정
        self.fc3 = nn.Linear(128, 64)   # 세 번째 은닉층 추가
        self.fc4 = nn.Linear(64, 32)    # 네 번째 은닉층 추가
        self.fc5 = nn.Linear(32, 1)     # 출력층
        self.relu = nn.ReLU()
        self.dropout = nn.Dropout(p=0.4)  # 드롭아웃 확률을 40%로 증가
        self.batch_norm1 = nn.BatchNorm1d(256)  # 배치 정규화 추가
        self.batch_norm2 = nn.BatchNorm1d(128)  # 배치 정규화 추가
        self.sigmoid = nn.Sigmoid()
    
    def forward(self, x):
        x = self.relu(self.batch_norm1(self.fc1(x)))
        x = self.dropout(self.relu(self.batch_norm2(self.fc2(x))))
        x = self.relu(self.fc3(x))
        x = self.relu(self.fc4(x))
        x = self.fc5(x)
        x = self.sigmoid(x)
        return x

# Initialize the enhanced model
model = EnhancedBinaryNN()

# Loss function and optimizer
criterion = nn.BCELoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

# Define the training function
def train_modified_model(X_train, y_train, model, criterion, optimizer, epochs):
    model.train()
    for epoch in range(epochs):
        optimizer.zero_grad()
        outputs = model(X_train).squeeze()
        loss = criterion(outputs, y_train)
        loss.backward()
        optimizer.step()
        if (epoch + 1) % 10 == 0:
            print(f"Epoch [{epoch + 1}/{epochs}], Loss: {loss.item():.4f}")

# Train the enhanced model
train_modified_model(X_train, y_train, model, criterion, optimizer, epochs=100)

# Evaluate the enhanced model
model.eval()
with torch.no_grad():
    y_pred_proba = model(X_test).squeeze()  # Predicted probabilities
    y_pred = (y_pred_proba > 0.5).float()  # Convert probabilities to binary predictions

    # Compute metrics
    accuracy = accuracy_score(y_test.numpy(), y_pred.numpy())
    precision = precision_score(y_test.numpy(), y_pred.numpy())
    recall = recall_score(y_test.numpy(), y_pred.numpy())
    f1 = f1_score(y_test.numpy(), y_pred.numpy())

    print(f"Accuracy: {accuracy * 100:.2f}%")
    print(f"Precision: {precision:.2f}")
    print(f"Recall: {recall:.2f}")
    print(f"F1 Score: {f1:.2f}")

# Save the enhanced model
torch.save(model.state_dict(), 'enhanced_binary_nn_model.pth')
print("Enhanced model saved to 'enhanced_binary_nn_model.pth'")




KeyError: '계열화'

#### 그냥 추천해줄 거 모두 출력 (기본 코드)

In [13]:
import pandas as pd
import torch
import torch.nn as nn
import torch.optim as optim
from collections import defaultdict
import re
import numpy as np
from scipy.spatial.distance import mahalanobis

class EnhancedBinaryNN(nn.Module):
    def __init__(self):
        super(EnhancedBinaryNN, self).__init__()
        # 더 깊고 복잡한 네트워크
        self.fc1 = nn.Linear(4, 256)  # 첫 번째 은닉층의 유닛 수를 256으로 증가
        self.fc2 = nn.Linear(256, 128)  # 두 번째 은닉층의 유닛 수를 128로 설정
        self.fc3 = nn.Linear(128, 64)   # 세 번째 은닉층 추가
        self.fc4 = nn.Linear(64, 32)    # 네 번째 은닉층 추가
        self.fc5 = nn.Linear(32, 1)     # 출력층
        self.relu = nn.ReLU()
        self.dropout = nn.Dropout(p=0.4)  # 드롭아웃 확률을 40%로 증가
        self.batch_norm1 = nn.BatchNorm1d(256)  # 배치 정규화 추가
        self.batch_norm2 = nn.BatchNorm1d(128)  # 배치 정규화 추가
        self.sigmoid = nn.Sigmoid()
    
    def forward(self, x):
        x = self.relu(self.batch_norm1(self.fc1(x)))
        x = self.dropout(self.relu(self.batch_norm2(self.fc2(x))))
        x = self.relu(self.fc3(x))
        x = self.relu(self.fc4(x))
        x = self.fc5(x)
        x = self.sigmoid(x)
        return x
        
# Load the model
model = EnhancedBinaryNN()
model.load_state_dict(torch.load('./enhanced_binary_nn_model.pth'))
model.eval()
print("Model loaded from 'enhanced_binary_nn_model.pth'")

# Utility functions
def extract_semester(semester_str):
    if pd.isna(semester_str):
        return ''
    match = re.search(r'(\d+)-(\d+)', semester_str)
    return (int(match.group(1)), int(match.group(2))) if match else (None, None)

def parse_series_order(order_str):
    if not order_str:
        return ('ZZZ', float('inf'), float('inf'))
    match = re.match(r'([A-Z]+)-(\d+)-(\d+)', order_str)
    if match:
        return (match.group(1), int(match.group(2)), int(match.group(3)))
    return ('ZZZ', float('inf'), float('inf'))

def get_unique_id_name_pairs(df):
    to_id_name = dict(zip(df['to_id'], df['to_chapter_name']))
    from_id_name = dict(zip(df['from_id'], df['from_chapter_name']))
    all_ids = set(to_id_name.keys()).union(set(from_id_name.keys()))
    unique_id_name_pairs = {}
    unique_id_semesters = {}
    for id_ in all_ids:
        to_name = to_id_name.get(id_, '')
        from_name = from_id_name.get(id_, '')
        if to_name and from_name:
            unique_id_name_pairs[id_] = f'{to_name} / {from_name}'
        elif to_name:
            unique_id_name_pairs[id_] = to_name
        elif from_name:
            unique_id_name_pairs[id_] = from_name
        from_semester = df[df['from_id'] == id_]['from_semester'].values
        to_semester = df[df['to_id'] == id_]['to_semester'].values
        if len(from_semester) > 0:
            unique_id_semesters[id_] = extract_semester(from_semester[0])
        elif len(to_semester) > 0:
            unique_id_semesters[id_] = extract_semester(to_semester[0])
        else:
            unique_id_semesters[id_] = (None, None)
    return unique_id_name_pairs, unique_id_semesters

# 본개념과 ID-이름 쌍, 학기 정보 가져오기
unique_id_name_pairs, unique_id_semesters = get_unique_id_name_pairs(label_math_ele)

# education_2022 데이터를 ID를 기준으로 매칭할 수 있도록 딕셔너리 생성
education_mapping = education_2022.set_index('ID').to_dict('index')
predecessors = defaultdict(list)
successors = defaultdict(list)

# to_id와 from_id로 연결 관계 설정
to_chapter_names = dict(zip(label_math_ele['to_id'], label_math_ele['to_chapter_name']))
from_chapter_names = dict(zip(label_math_ele['from_id'], label_math_ele['from_chapter_name']))
for _, row in label_math_ele.iterrows():
    from_id = row['from_id']
    to_id = row['to_id']
    predecessors[from_id].append(to_id)
    successors[to_id].append(from_id)

def analyze_student_performance(learner_id, df):
    student_df = df[df['learnerID'] == learner_id].copy()
    if student_df.empty:
        print(f"학습자 {learner_id}의 데이터가 없습니다.")
        return None, None
    if student_df['answerCode'].dtype == 'object':
        student_df['answerCode'] = pd.to_numeric(student_df['answerCode'], errors='coerce')
    correct_df = student_df[student_df['answerCode'] == 1]
    incorrect_df = student_df[student_df['answerCode'] == 0]
    return correct_df['knowledgeTag'].tolist(), incorrect_df['knowledgeTag'].tolist()

def get_concepts(node_id, unique_id_name_pairs, unique_id_semesters, education_mapping, predecessors, successors):
    main_concept = {
        '본개념': node_id,
        '본개념_Chapter_Name': unique_id_name_pairs.get(node_id, '정보 없음'),
        '학년-학기': unique_id_semesters.get(node_id, (None, None))
    }
    main_concept['선수학습'] = sorted(
        predecessors.get(node_id, []),
        key=lambda x: parse_series_order(education_mapping.get(x, {}).get('계열화', '')),
        reverse=True
    )
    main_concept['후속학습'] = sorted(
        successors.get(node_id, []),
        key=lambda x: parse_series_order(education_mapping.get(x, {}).get('계열화', ''))
    )
    return main_concept

def exclude_correct_predecessors_from_incorrect(correct_preds, incorrect_preds):
    correct_set = set(id_name for preds in correct_preds.values() for id_name in preds)
    incorrect_set = set(id_name for preds in incorrect_preds.values() for id_name in preds)
    return incorrect_set - correct_set

def get_chapter_serialization_info(predecessor_ids, unique_id_name_pairs, education_mapping):
    serialization_info = []
    for id_ in predecessor_ids:
        chapter_name = unique_id_name_pairs.get(id_, '정보 없음')
        info = education_mapping.get(id_, {})
        serialization = info.get('계열화', '정보 없음')
        serialization_info.append({
            '선수학습_ID': id_,
            '선수학습_Chapter_Name': chapter_name,
            '계열화': serialization
        })
    return pd.DataFrame(serialization_info)

def extract_first_part(df):
    df['첫 번째 부분'] = df['계열화'].apply(lambda x: x.split('>')[0].strip())
    return df[['knowledgeTag', '첫 번째 부분']]

def filter_successor_recommendations(successor_df, prerequisite_areas):
    prerequisite_parts = prerequisite_areas['첫 번째 부분'].unique()
    filtered_successors = successor_df[~successor_df['계열화'].apply(lambda x: x.split('>')[0].strip()).isin(prerequisite_parts)]
    return filtered_successors

def extract_prefix(serialization_code):
    # Extract prefix from serialization code (before the first dash or space)
    return serialization_code.split('-')[0] if '-' in serialization_code else serialization_code.split(' ')[0]

def recommend_concept(learner_id, df, model, unique_id_name_pairs, unique_id_semesters, education_mapping, predecessors, successors):
    correct_knowledge_tags, incorrect_knowledge_tags = analyze_student_performance(learner_id, df)
    if correct_knowledge_tags is None or incorrect_knowledge_tags is None:
        return pd.DataFrame(), pd.DataFrame()  # Return empty DataFrames if no data

    # Get predecessors for correct and incorrect problems
    correct_predecessors = {tag: get_concepts(tag, unique_id_name_pairs, unique_id_semesters, education_mapping, predecessors, successors)['선수학습'] for tag in correct_knowledge_tags}
    incorrect_predecessors = {tag: get_concepts(tag, unique_id_name_pairs, unique_id_semesters, education_mapping, predecessors, successors)['선수학습'] for tag in incorrect_knowledge_tags}
    
    # Filter out concepts unique to incorrect predecessors
    unique_incorrect_only_preds = exclude_correct_predecessors_from_incorrect(correct_predecessors, incorrect_predecessors)

    # 교집합 없는 경우 처리
    if not unique_incorrect_only_preds:
        print("교집합이 없는 학생입니다. 선행학습만 추천합니다.")
        # 후속 학습 추천 로직
        successor_recommendations_df = recommend_successors_based_on_previous_learning(
            incorrect_knowledge_tags, unique_id_name_pairs, education_mapping, predecessors, successors
        )
        return pd.DataFrame(), successor_recommendations_df

    # 기존의 로직
    serialization_info_df = get_chapter_serialization_info(unique_incorrect_only_preds, unique_id_name_pairs, education_mapping)

    # Prepare student data for model input
    student_df = df[df['learnerID'] == learner_id]
    if 'weighted_score' not in student_df.columns:
        student_df['weighted_score'] = 1
    X_student = student_df[['difficultyLevel', 'discriminationLevel', 'theta', 'guessLevel']].values
    X_student_tensor = torch.tensor(X_student, dtype=torch.float32)
    
    # Make predictions using the model
    model.eval()
    with torch.no_grad():
        model_output = model(X_student_tensor).squeeze().numpy()
    
    # Check if model_output is not empty
    if model_output.size == 0:
        print("Error: Model output is empty.")
        return pd.DataFrame(), pd.DataFrame()
    
    # Add prediction probabilities to student_df
    student_df['predicted_probability'] = model_output

    # Check if 'predicted_probability' column is created
    if 'predicted_probability' not in student_df.columns:
        print("Error: 'predicted_probability' column is missing in student_df.")
        return pd.DataFrame(), pd.DataFrame()

    # Prepare recommendations based on predicted probabilities
    recommendations = []
    for _, row in serialization_info_df.iterrows():
        concept_id = row['선수학습_ID']
        if concept_id in student_df['knowledgeTag'].values:
            prob = student_df[student_df['knowledgeTag'] == concept_id]['predicted_probability'].values
            probability = prob[0] if prob.size > 0 else 0.0
            recommendations.append({
                'knowledgeTag': concept_id,
                'predicted_probability': probability,
                '선수학습_Chapter_Name': row['선수학습_Chapter_Name'],
                '계열화': row['계열화']
            })
    
    # Convert recommendations to DataFrame
    recommendations_df = pd.DataFrame(recommendations)

    # Handle the case when recommendations_df is empty
    if recommendations_df.empty:
        print("추천 결과가 없습니다.")
        successor_recommendations_df = recommend_successors_based_on_previous_learning(
            incorrect_knowledge_tags, unique_id_name_pairs, education_mapping, predecessors, successors
        )
        return recommendations_df, successor_recommendations_df

    # Check if 'predicted_probability' column is present in recommendations_df
    if 'predicted_probability' not in recommendations_df.columns:
        print("Error: 'predicted_probability' column is missing in recommendations_df.")
    
    recommendations_df = recommendations_df.sort_values(by='predicted_probability', ascending=False)
    
    # Extract successor recommendations (기존 로직 유지)
    successor_recommendations = []
    for tag in incorrect_knowledge_tags:
        concepts = get_concepts(tag, unique_id_name_pairs, unique_id_semesters, education_mapping, predecessors, successors)
        for succ in concepts['후속학습']:
            successor_area = extract_prefix(education_mapping.get(succ, {}).get('계열화', '정보 없음'))
            if successor_area not in [extract_prefix(x) for x in serialization_info_df['계열화']]:
                successor_recommendations.append({
                    'knowledgeTag': succ,
                    'predicted_probability': 0.0,
                    '후속학습_Chapter_Name': unique_id_name_pairs.get(succ, '정보 없음'),
                    '계열화': education_mapping.get(succ, {}).get('계열화', '정보 없음')
                })
    
    # Convert successor recommendations to DataFrame
    successor_recommendations_df = pd.DataFrame(successor_recommendations)
    
    # Calculate Mahalanobis distance for successor recommendations
    if not successor_recommendations_df.empty:
        correct_answers = df[df['answerCode'] == 1]
        mean_correct = correct_answers[['difficultyLevel', 'discriminationLevel', 'guessLevel']].mean().values
        cov_correct = np.cov(correct_answers[['difficultyLevel', 'discriminationLevel', 'guessLevel']], rowvar=False)
        
        distances = {}
        for _, row in successor_recommendations_df.iterrows():
            knowledge_tag = row['knowledgeTag']
            if knowledge_tag in df['knowledgeTag'].values:
                row_data = df[df['knowledgeTag'] == knowledge_tag][['difficultyLevel', 'discriminationLevel', 'guessLevel']].mean().values
                distance = mahalanobis(row_data, mean_correct, np.linalg.inv(cov_correct))
                distances[knowledge_tag] = distance
        
        successor_recommendations_df['Mahalanobis_distance'] = successor_recommendations_df['knowledgeTag'].apply(lambda x: distances.get(x, float('inf')))
        successor_recommendations_df = successor_recommendations_df.sort_values(by='Mahalanobis_distance', ascending=True)

    return recommendations_df, successor_recommendations_df

def recommend_successors_based_on_previous_learning(incorrect_knowledge_tags, unique_id_name_pairs, education_mapping, predecessors, successors):
    # Use the existing function for successor recommendations if necessary
    successor_recommendations = []
    for tag in incorrect_knowledge_tags:
        concepts = get_concepts(tag, unique_id_name_pairs, unique_id_semesters, education_mapping, predecessors, successors)
        for succ in concepts['후속학습']:
            successor_area = extract_prefix(education_mapping.get(succ, {}).get('계열화', '정보 없음'))
            successor_recommendations.append({
                'knowledgeTag': succ,
                'predicted_probability': 0.0,
                '후속학습_Chapter_Name': unique_id_name_pairs.get(succ, '정보 없음'),
                '계열화': education_mapping.get(succ, {}).get('계열화', '정보 없음')
            })
    
    # Convert successor recommendations to DataFrame
    successor_recommendations_df = pd.DataFrame(successor_recommendations)
    
    # Calculate Mahalanobis distance for successor recommendations
    if not successor_recommendations_df.empty:
        correct_answers = merged_df[merged_df['answerCode'] == 1]
        mean_correct = correct_answers[['difficultyLevel', 'discriminationLevel', 'guessLevel']].mean().values
        cov_correct = np.cov(correct_answers[['difficultyLevel', 'discriminationLevel', 'guessLevel']], rowvar=False)
        
        distances = {}
        for _, row in successor_recommendations_df.iterrows():
            knowledge_tag = row['knowledgeTag']
            if knowledge_tag in merged_df['knowledgeTag'].values:
                row_data = merged_df[merged_df['knowledgeTag'] == knowledge_tag][['difficultyLevel', 'discriminationLevel', 'guessLevel']].mean().values
                distance = mahalanobis(row_data, mean_correct, np.linalg.inv(cov_correct))
                distances[knowledge_tag] = distance
        
        successor_recommendations_df['Mahalanobis_distance'] = successor_recommendations_df['knowledgeTag'].apply(lambda x: distances.get(x, float('inf')))
        successor_recommendations_df = successor_recommendations_df.sort_values(by='Mahalanobis_distance', ascending=True)

    return successor_recommendations_df



def recommend_all(learner_id, df, model, unique_id_name_pairs, unique_id_semesters, education_mapping, predecessors, successors):
    # Get recommendations for prerequisites
    prerequisite_recommendations, successor_recommendations = recommend_concept(
        learner_id, df, model, unique_id_name_pairs, unique_id_semesters, education_mapping, predecessors, successors
    )
    
    # Check if prerequisite recommendations are empty and handle accordingly
    if prerequisite_recommendations.empty:
        print("선수학습 개념이 없으므로 후속 학습 개념을 추천합니다.")
        return pd.DataFrame(), successor_recommendations

    return prerequisite_recommendations, successor_recommendations


def map_area(serialization_code):
    # Define the mapping from serialization code to area
    area_mapping = {
        'A': '수와 연산',
        'B': '변화와 관계',
        'C': '도형',
        'D': '측정',
        'E': '자료와 가능성'
    }
    
    # Extract the prefix from serialization code
    prefix = extract_prefix(serialization_code)
    
    # Map the prefix to area
    return area_mapping.get(prefix, '기타')

def recommend_one_per_area(recommendations_df):
    # Check if 'predicted_probability' column is present
    if 'predicted_probability' not in recommendations_df.columns:
        print("Error: 'predicted_probability' column is missing in recommendations_df.")
        print("선수학습 개념이 없습니다.")  # Print a message in case no recommendations are available
        return pd.DataFrame()  # Return an empty DataFrame

    # Filter out rows where '계열화' is '정보 없음'
    recommendations_df = recommendations_df[recommendations_df['계열화'] != '정보 없음']
    
    # Add '영역' column based on '계열화'
    recommendations_df['영역'] = recommendations_df['계열화'].apply(map_area)
    
    # Group by '영역' and select the highest predicted probability in each group
    top_recommendations = recommendations_df.loc[
        recommendations_df.groupby('영역')['predicted_probability'].idxmax()
    ]
    
    # Sort by predicted probability in descending order
    top_recommendations = top_recommendations.sort_values(by='predicted_probability', ascending=False)
    
    # Remove unnecessary columns
    top_recommendations = top_recommendations.drop(columns=['predicted_probability'])
    
    return top_recommendations


def recommend_one_per_area_successors(successor_recommendations_df):
    # Filter out rows where '계열화' is '정보 없음'
    successor_recommendations_df = successor_recommendations_df[successor_recommendations_df['계열화'] != '정보 없음']
    
    # Add '영역' column based on '계열화'
    successor_recommendations_df['영역'] = successor_recommendations_df['계열화'].apply(map_area)
    
    # Group by '영역' and select the closest Mahalanobis distance in each group
    top_successor_recommendations = successor_recommendations_df.loc[
        successor_recommendations_df.groupby('영역')['Mahalanobis_distance'].idxmin()
    ]
    
    # Sort by Mahalanobis distance in ascending order
    top_successor_recommendations = top_successor_recommendations.sort_values(by='Mahalanobis_distance', ascending=True)
    
    # Remove unnecessary columns
    top_successor_recommendations = top_successor_recommendations.drop(columns=['predicted_probability', 'Mahalanobis_distance'])
    
    return top_successor_recommendations

# Example usage
while True:
    learner_id_input = input("학습자 ID를 입력하세요: ").strip()
    
    # 학습자 ID 존재 여부 확인
    if learner_id_input not in merged_df['learnerID'].unique():
        print("존재하지 않는 학습자입니다. 다시 입력하세요.")
        continue
    
    # 추천 데이터 생성
    prerequisite_recommendations_df, successor_recommendations_df = recommend_all(
        learner_id_input, merged_df, model, unique_id_name_pairs, unique_id_semesters, education_2022.set_index('ID').to_dict('index'), predecessors, successors
    )
    
    # 추천할 내용이 있는지 확인ㅊ
    if prerequisite_recommendations_df.empty and successor_recommendations_df.empty:
        print("추천할 이전 학습 개념이 없습니다.")
    else:
        # 추천할 항목이 있으면 출력
        top_prerequisite_recommendations_df = recommend_one_per_area(prerequisite_recommendations_df)
        top_successor_recommendations_df = recommend_one_per_area_successors(successor_recommendations_df)
        
        print(f"Top recommended prerequisites for learner {learner_id_input}:")
        print(top_prerequisite_recommendations_df)
        
        print(f"Top recommended successors for learner {learner_id_input}:")
        print(top_successor_recommendations_df)
    
    # 입력 루프 종료
    break


Model loaded from 'enhanced_binary_nn_model.pth'


C:\Users\user\AppData\Local\Temp\ipykernel_18896\37997730.py:183: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  student_df['weighted_score'] = 1
C:\Users\user\AppData\Local\Temp\ipykernel_18896\37997730.py:198: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  student_df['predicted_probability'] = model_output


Top recommended prerequisites for learner A040000079:
    knowledgeTag                                  선수학습_Chapter_Name    계열화  \
8           2097  분수의 덧셈과 뺄셈 > 분수의 뺄셈을 해 볼까요 (1) / 분수의 덧셈과 뺄셈 > ...  A-9-3   
5           2085        막대그래프 > 막대그래프를 알아볼까요 / 막대그래프 > 막대그래프를 알아볼까요  E-5-1   
6           2092  규칙 찾기 > 계산식에서 규칙을 찾아볼까요 (1) / 규칙 찾기 > 계산식에서 규칙...  B-2-4   
12          2127  꺾은선그래프 > 꺾은선그래프를 어떻게 그릴까요 / 꺾은선그래프 > 꺾은선그래프를 어...  D-9-4   

         영역  
8     수와 연산  
5   자료와 가능성  
6    변화와 관계  
12       측정  
Top recommended successors for learner A040000079:
     knowledgeTag                    후속학습_Chapter_Name    계열화  영역
353          2123  사각형 > 마름모를 알아볼까요 / 사각형 > 마름모를 알아볼까요  C-6-8  도형


C:\Users\user\AppData\Local\Temp\ipykernel_18896\37997730.py:372: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  successor_recommendations_df['영역'] = successor_recommendations_df['계열화'].apply(map_area)


In [14]:
top_prerequisite_recommendations_df

knowledgeTag                                  선수학습_Chapter_Name    계열화  \
8           2097  분수의 덧셈과 뺄셈 > 분수의 뺄셈을 해 볼까요 (1) / 분수의 덧셈과 뺄셈 > ...  A-9-3   
5           2085        막대그래프 > 막대그래프를 알아볼까요 / 막대그래프 > 막대그래프를 알아볼까요  E-5-1   
6           2092  규칙 찾기 > 계산식에서 규칙을 찾아볼까요 (1) / 규칙 찾기 > 계산식에서 규칙...  B-2-4   
12          2127  꺾은선그래프 > 꺾은선그래프를 어떻게 그릴까요 / 꺾은선그래프 > 꺾은선그래프를 어...  D-9-4   

         영역  
8     수와 연산  
5   자료와 가능성  
6    변화와 관계  
12       측정

In [15]:
top_successor_recommendations_df

knowledgeTag                    후속학습_Chapter_Name    계열화  영역
353          2123  사각형 > 마름모를 알아볼까요 / 사각형 > 마름모를 알아볼까요  C-6-8  도형

# 한 학생의 선,후 학습 db에 적재

In [16]:
from sqlalchemy import create_engine, inspect, MetaData, Table, Column, String, PrimaryKeyConstraint
import pandas as pd

def save_recommendations_to_db(learner_id, prerequisite_df, successor_df, engine):
    # 데이터프레임에 learner_id 컬럼 추가
    prerequisite_df['learner_id'] = learner_id
    successor_df['learner_id'] = learner_id

    # 컬럼 확인 및 출력
    print("prerequisite_df columns:", prerequisite_df.columns)
    print("successor_df columns:", successor_df.columns)
    
    # 필요한 컬럼 및 기본값 정의
    prerequisite_required_columns = ['learner_id', 'knowledgeTag', '선수학습_Chapter_Name', '계열화', '영역']
    successor_required_columns = ['learner_id', 'knowledgeTag', '후속학습_Chapter_Name', '계열화', '영역']
    
    prerequisite_default_values = {'knowledgeTag': 'N/A', '선수학습_Chapter_Name': 'N/A', '계열화': 'N/A', '영역': 'N/A'}
    successor_default_values = {'knowledgeTag': 'N/A', '후속학습_Chapter_Name': 'N/A', '계열화': 'N/A', '영역': 'N/A'}

    def adjust_columns(df, required_columns, default_values):
        existing_columns = df.columns
        columns_to_use = [col for col in required_columns if col in existing_columns]
        for col, default_value in default_values.items():
            if col not in df.columns:
                df[col] = default_value
        return df[columns_to_use]

    prerequisite_df = adjust_columns(prerequisite_df, prerequisite_required_columns, prerequisite_default_values)
    successor_df = adjust_columns(successor_df, successor_required_columns, successor_default_values)

    # 중복 제거
    prerequisite_df = prerequisite_df.drop_duplicates()
    successor_df = successor_df.drop_duplicates()

    # 데이터 타입 일치시키기
    prerequisite_df['knowledgeTag'] = prerequisite_df['knowledgeTag'].astype(str)
    successor_df['knowledgeTag'] = successor_df['knowledgeTag'].astype(str)

    def create_table_if_not_exists(table_name, columns):
        with engine.connect() as conn:
            inspector = inspect(engine)
            if table_name not in inspector.get_table_names():
                metadata = MetaData()
                table = Table(table_name, metadata, *columns)
                metadata.create_all(engine)
                print(f"테이블 '{table_name}'이(가) 생성되었습니다.")

    # 테이블 생성 정의
    columns_prerequisite = [
        Column('learner_id', String, nullable=False),
        Column('knowledgeTag', String, nullable=False),
        Column('선수학습_Chapter_Name', String, nullable=True),
        Column('계열화', String, nullable=True),
        Column('영역', String, nullable=True),
        PrimaryKeyConstraint('learner_id', 'knowledgeTag', '선수학습_Chapter_Name')
    ]

    columns_successor = [
        Column('learner_id', String, nullable=False),
        Column('knowledgeTag', String, nullable=False),
        Column('후속학습_Chapter_Name', String, nullable=True),
        Column('계열화', String, nullable=True),
        Column('영역', String, nullable=True),
        PrimaryKeyConstraint('learner_id', 'knowledgeTag', '후속학습_Chapter_Name')
    ]

    # 테이블 생성 호출
    create_table_if_not_exists('prerequisite_recommendations', columns_prerequisite)
    create_table_if_not_exists('successor_recommendations', columns_successor)

    try:
        # PostgreSQL 데이터베이스에 저장
        with engine.connect() as conn:
            # 기존 데이터베이스와 중복된 데이터가 있는지 확인하고 삭제
            for table, df in [('prerequisite_recommendations', prerequisite_df),
                              ('successor_recommendations', successor_df)]:
                if not df.empty:  # 데이터프레임이 비어 있지 않은 경우만 처리
                    existing_data = pd.read_sql_table(table, conn)
                    
                    # 데이터 타입 일치시키기
                    existing_data['knowledgeTag'] = existing_data['knowledgeTag'].astype(str)
                    
                    # 중복된 데이터 확인
                    merged_data = pd.merge(df, existing_data, how='left', indicator=True)
                    new_data = merged_data[merged_data['_merge'] == 'left_only'].drop('_merge', axis=1)
                    new_data.to_sql(table, conn, if_exists='append', index=False)
                else:
                    print(f"데이터프레임이 비어 있습니다: {table} 테이블에 데이터가 없습니다.")

        print(f"학습자 ID {learner_id}에 대한 추천 사항이 데이터베이스에 성공적으로 저장되었습니다.")
    except Exception as e:
        print(f"추천 사항을 데이터베이스에 저장하는 중 오류가 발생했습니다: {e}")

# 추천 데이터를 데이터베이스에 저장
save_recommendations_to_db(learner_id_input, top_prerequisite_recommendations_df, top_successor_recommendations_df, engine)


prerequisite_df columns: Index(['knowledgeTag', '선수학습_Chapter_Name', '계열화', '영역', 'learner_id'], dtype='object')
successor_df columns: Index(['knowledgeTag', '후속학습_Chapter_Name', '계열화', '영역', 'learner_id'], dtype='object')
테이블 'prerequisite_recommendations'이(가) 생성되었습니다.
테이블 'successor_recommendations'이(가) 생성되었습니다.
학습자 ID A040000079에 대한 추천 사항이 데이터베이스에 성공적으로 저장되었습니다.


# 모든 학생들의 선,후학습 db에 적재

In [9]:
from sqlalchemy import create_engine

# PostgreSQL 연결 정보 설정
db_config = {
    'user': 'postgres',
    'password': 'qwe123',
    'host': '10.41.2.78',
    'port': '5432',
    'database': 'project'
}

# SQLAlchemy 엔진 생성
engine = create_engine(f"postgresql://{db_config['user']}:{db_config['password']}@{db_config['host']}:{db_config['port']}/{db_config['database']}")


In [17]:
import pandas as pd

def save_recommendations_to_db(learner_id, prerequisite_df, successor_df, engine):
    # 데이터프레임의 열 이름 확인
    print("Prerequisite DataFrame columns:", prerequisite_df.columns)
    print("Successor DataFrame columns:", successor_df.columns)

    # 데이터프레임에 learner_id 컬럼 추가 및 순서 재조정
    prerequisite_df['learner_id'] = learner_id
    successor_df['learner_id'] = learner_id

    # 필요한 열이 있는지 확인 후 데이터프레임 구성
    prerequisite_columns = ['learner_id', 'knowledgeTag', '선수학습_Chapter_Name', '계열화', '영역']
    successor_columns = ['learner_id', 'knowledgeTag', '후속학습_Chapter_Name', '계열화', '영역']

    # prerequisite_df에 필요한 열이 없으면 기본값으로 채우기
    for col in prerequisite_columns:
        if col not in prerequisite_df.columns:
            prerequisite_df[col] = None

    # 열 순서 맞추기
    prerequisite_df = prerequisite_df[prerequisite_columns]
    successor_df = successor_df[successor_columns]

    # 데이터프레임 열의 데이터 타입 일치 시키기
    prerequisite_df['knowledgeTag'] = pd.to_numeric(prerequisite_df['knowledgeTag'], errors='coerce', downcast='integer')
    successor_df['knowledgeTag'] = pd.to_numeric(successor_df['knowledgeTag'], errors='coerce', downcast='integer')

    # 중복 제거
    prerequisite_df = prerequisite_df.drop_duplicates()
    successor_df = successor_df.drop_duplicates()

    try:
        # PostgreSQL 데이터베이스에 저장
        with engine.connect() as conn:
            # 각 데이터프레임이 비어 있는지 확인하고, 비어 있지 않은 경우에만 저장
            if not prerequisite_df.empty:
                existing_data = pd.read_sql_table('prerequisite_recommendations', conn)
                existing_data['knowledgeTag'] = pd.to_numeric(existing_data['knowledgeTag'], errors='coerce', downcast='integer')
                merged_data = pd.merge(prerequisite_df, existing_data, how='left', indicator=True)
                new_data = merged_data[merged_data['_merge'] == 'left_only'].drop('_merge', axis=1)
                new_data.to_sql('prerequisite_recommendations', conn, if_exists='append', index=False)
            
            if not successor_df.empty:
                existing_data = pd.read_sql_table('successor_recommendations', conn)
                existing_data['knowledgeTag'] = pd.to_numeric(existing_data['knowledgeTag'], errors='coerce', downcast='integer')
                merged_data = pd.merge(successor_df, existing_data, how='left', indicator=True)
                new_data = merged_data[merged_data['_merge'] == 'left_only'].drop('_merge', axis=1)
                new_data.to_sql('successor_recommendations', conn, if_exists='append', index=False)

        print(f"학습자 ID {learner_id}에 대한 추천 사항이 데이터베이스에 성공적으로 저장되었습니다.")
    except Exception as e:
        print(f"추천 사항을 데이터베이스에 저장하는 중 오류가 발생했습니다: {e}")

# 필터링할 learner IDs 및 추천 데이터프레임 정의
prefixes = ['A01', 'A02', 'A03', 'A04', 'A05', 'A06']
filtered_learner_ids = merged_df[merged_df['learnerID'].str.startswith(tuple(prefixes))]['learnerID'].unique()

# 각 learner_id에 대해 save_recommendations_to_db 함수 호출
for learner_id in filtered_learner_ids:
    # top_prerequisite_recommendations_df와 top_successor_recommendations_df를 해당 learner_id에 맞게 필터링하거나 생성해야 함
    # 여기에 맞는 코드 추가 필요
    save_recommendations_to_db(learner_id, top_prerequisite_recommendations_df, top_successor_recommendations_df, engine)

Prerequisite DataFrame columns: Index(['knowledgeTag', '선수학습_Chapter_Name', '계열화', '영역', 'learner_id'], dtype='object')
Successor DataFrame columns: Index(['knowledgeTag', '후속학습_Chapter_Name', '계열화', '영역', 'learner_id'], dtype='object')
학습자 ID A010000003에 대한 추천 사항이 데이터베이스에 성공적으로 저장되었습니다.
Prerequisite DataFrame columns: Index(['knowledgeTag', '선수학습_Chapter_Name', '계열화', '영역', 'learner_id'], dtype='object')
Successor DataFrame columns: Index(['knowledgeTag', '후속학습_Chapter_Name', '계열화', '영역', 'learner_id'], dtype='object')
학습자 ID A010000006에 대한 추천 사항이 데이터베이스에 성공적으로 저장되었습니다.
Prerequisite DataFrame columns: Index(['knowledgeTag', '선수학습_Chapter_Name', '계열화', '영역', 'learner_id'], dtype='object')
Successor DataFrame columns: Index(['knowledgeTag', '후속학습_Chapter_Name', '계열화', '영역', 'learner_id'], dtype='object')
학습자 ID A010000008에 대한 추천 사항이 데이터베이스에 성공적으로 저장되었습니다.
Prerequisite DataFrame columns: Index(['knowledgeTag', '선수학습_Chapter_Name', '계열화', '영역', 'learner_id'], dtype='object')
Successor Dat